# Post-Experimental Data Visualization

In [23]:
import itertools
import json
import numpy as np
from os import path
import pandas as pd
import pickle
import plotly.figure_factory as ff
import skimage 
from pse import gp


In [24]:
# df = pd.read_json("results.json")

## Variables

In [25]:
spath = 'phase_space'
stock_conc_DOPC = 5
stock_conc_DOPE = 2
stock_conc_POPG = 4

new_stepsize = 0.1

## Load Data and recreate PSE Object

In [26]:
with open("results.json", "r") as f:
    results_data = json.load(f)

In [27]:
with open(path.join(spath, 'pse_parameters.pkl'), 'rb') as file:
    pse_pars = pickle.load(file)

pse_pars = pd.DataFrame(pse_pars)

if new_stepsize is not None:
    pse_pars['step_opt'] = new_stepsize
    
pse_pars

name      type  value  lower_opt  upper_opt  optimize  step_opt
0  DOPC  compound    1.0        0.0        1.0      True       0.1
1  DOPE  compound    1.0        0.0        1.0      True       0.1
2  POPG  compound    1.0        0.0        1.0      True       0.1

## Regenerate Prediction GP prediction

In [28]:
gpo = gp.Gp(exp_par=pse_pars, storage_path=spath, resume=True)
gpo.gpcam_init_ae()
gpo.gpcam_train()
gpo.gpcam_prediction()

length of the dataset:  32


/Users/frank/opt/anaconda3/envs/phasespace/lib/python3.12/site-packages/fvgp/gp_training.py:234: RuntimeWarning:

Method L-BFGS-B does not use Hessian information (hess).



In [29]:
prediction = gpo.prediction_gpcam
axes = gpo.axes
label_combinations = list(itertools.product(*axes))
values = prediction.flatten()

prediction_df = pd.DataFrame(label_combinations, columns=[pse_pars['name'][i]+'_opt' for i in range(prediction.ndim)])
prediction_df['PSE_result'] = values
prediction_df

DOPC_opt  DOPE_opt  POPG_opt  PSE_result
0          0.0       0.0       0.0  -14.634105
1          0.0       0.0       0.1  -13.866163
2          0.0       0.0       0.2  -13.105710
3          0.0       0.0       0.3  -12.359695
4          0.0       0.0       0.4  -11.636093
...        ...       ...       ...         ...
1326       1.0       1.0       0.6  -23.393244
1327       1.0       1.0       0.7  -23.224057
1328       1.0       1.0       0.8  -23.087588
1329       1.0       1.0       0.9  -22.988047
1330       1.0       1.0       1.0  -22.929980

[1331 rows x 4 columns]

## Transform Parameters

In [30]:
prediction_df['DOPC_opt_trans'] = prediction_df['DOPC_opt']
prediction_df['DOPE_opt_trans'] = (1 - prediction_df['DOPC_opt_trans']) * prediction_df['DOPE_opt']
prediction_df['POPG_opt_trans'] = (1 - prediction_df['DOPC_opt_trans'] - prediction_df['DOPE_opt_trans']) * prediction_df['POPG_opt']
prediction_df['DOPC_conc'] = prediction_df['DOPC_opt_trans'] * stock_conc_DOPC
prediction_df['DOPE_conc'] = prediction_df['DOPE_opt_trans'] * stock_conc_DOPC
prediction_df['POPG_conc'] = prediction_df['POPG_opt_trans'] * stock_conc_DOPC
prediction_df['total_conc'] = prediction_df['DOPC_conc'] + prediction_df['DOPE_conc'] + prediction_df['POPG_conc']

prediction_df['DOPC_frac'] = prediction_df['DOPC_opt_trans'] / (prediction_df['DOPC_opt_trans'] + prediction_df['DOPE_opt_trans'] + prediction_df['POPG_opt_trans'])
prediction_df['DOPE_frac'] = prediction_df['DOPE_opt_trans'] / (prediction_df['DOPC_opt_trans'] + prediction_df['DOPE_opt_trans'] + prediction_df['POPG_opt_trans'])
prediction_df['POPG_frac'] = prediction_df['POPG_opt_trans'] / (prediction_df['DOPC_opt_trans'] + prediction_df['DOPE_opt_trans'] + prediction_df['POPG_opt_trans'])

prediction_df.loc[0, 'DOPC_frac'] = 1/3
prediction_df.loc[0, 'DOPE_frac'] = 1/3
prediction_df.loc[0, 'POPG_frac'] = 1/3

prediction_df

DOPC_opt  DOPE_opt  POPG_opt  PSE_result  DOPC_opt_trans  \
0          0.0       0.0       0.0  -14.634105             0.0   
1          0.0       0.0       0.1  -13.866163             0.0   
2          0.0       0.0       0.2  -13.105710             0.0   
3          0.0       0.0       0.3  -12.359695             0.0   
4          0.0       0.0       0.4  -11.636093             0.0   
...        ...       ...       ...         ...             ...   
1326       1.0       1.0       0.6  -23.393244             1.0   
1327       1.0       1.0       0.7  -23.224057             1.0   
1328       1.0       1.0       0.8  -23.087588             1.0   
1329       1.0       1.0       0.9  -22.988047             1.0   
1330       1.0       1.0       1.0  -22.929980             1.0   

      DOPE_opt_trans  POPG_opt_trans  DOPC_conc  DOPE_conc  POPG_conc  \
0                0.0             0.0        0.0        0.0        0.0   
1                0.0             0.1        0.0        0.0        0.5   
2                0.0             0.2        0.0        0.0        1.0   
3                0.0             0.3        0.0        0.0        1.5   
4                0.0             0.4        0.0        0.0        2.0   
...              ...             ...        ...        ...        ...   
1326             0.0             0.0        5.0        0.0        0.0   
1327             0.0             0.0        5.0        0.0        0.0   
1328             0.0             0.0        5.0        0.0        0.0   
1329             0.0             0.0        5.0        0.0        0.0   
1330             0.0             0.0        5.0        0.0        0.0   

      total_conc  DOPC_frac  DOPE_frac  POPG_frac  
0            0.0   0.333333   0.333333   0.333333  
1            0.5   0.000000   0.000000   1.000000  
2            1.0   0.000000   0.000000   1.000000  
3            1.5   0.000000   0.000000   1.000000  
4            2.0   0.000000   0.000000   1.000000  
...          ...        ...        ...        ...  
1326         5.0   1.000000   0.000000   0.000000  
1327         5.0   1.000000   0.000000   0.000000  
1328         5.0   1.000000   0.000000   0.000000  
1329         5.0   1.000000   0.000000   0.000000  
1330         5.0   1.000000   0.000000   0.000000  

[1331 rows x 14 columns]

# Plotting

In [99]:
conc_min = 2
conc_max = 6
target_result = None

if conc_min is not None and conc_max is not None:
    prediction_df2 = prediction_df[(prediction_df['total_conc'] >= conc_min) & (prediction_df['total_conc'] <= conc_max)]
else:
    prediction_df2 = prediction_df.copy()

In [100]:
plotly_axes = prediction_df2[['DOPC_frac', 'DOPE_frac', 'POPG_frac']].to_numpy().transpose()
plotly_data = prediction_df2[['PSE_result']].to_numpy().transpose()[0]
plotly_labels = ['DOPC', 'DOPE', 'POPG']

if target_result is not None:
    v = np.abs(-28 - plotly_data[:])
else:
    v = plotly_data[:]

fig = ff.create_ternary_contour( 
    plotly_axes, v, 
    width=1000,
    height=800,
    pole_labels=plotly_labels,
    interp_mode='cartesian',
    coloring = None,
    ncontours=None,
    colorscale='Viridis',
    showscale=True,
    title=dict(
        text='PSE result difference from -28'
    )
)
  
fig.show() 